<div align="center"><font size=2>FORCeS eScience course 2021 - “Tools in Climate Science: Linking Observations with Modelling”</font></div>
<br>
<img src='https://www.reliance-project.eu/wp-content/uploads/2021/03/Asset-8mdpi.svg' alt='Layout' align='left' width='25%'></img> 
<img src='https://media-exp1.licdn.com/dms/image/C560BAQFFDze0s3l-pQ/company-logo_200_200/0?e=2159024400&v=beta&t=jG_sh9NpwE6yc2TspIcL2YUR2X7OBzTrRSu6w7sNYtc' alt='Layout' align='right' width='10%'></img> 
<br>
<br>
<br>
<div align="center"><font size=20><b>My Final report</b></font></div>
<div align="center"><font size=6>Anne Fouilloux</font></div>
<div align="center"><font size=4>annefou-at-uio.no</font></div>
<div align="center"><font size=4><b>Assistant: XXX</b></font></div>
<br>
<br>
<br>
<br>

# Final Report

## Abstract 

Write a short abstract here. 1/2 page max should be sufficient.

## Acknowledgements

The computing resources used for this course have been kindly provided by Galaxy europe in the framework of the [EOSC-Nordic](https://www.eosc-nordic.eu/) and [RELIANCE](https://www.reliance-project.eu/) projects. The storage resources were provided by [UNINETT Sigma2](https://www.sigma2.no/) - the Norwegian National Infrastructure for High Performance Computing and Data Storage in Norway as part of NS1000K project.


<div class="alert alert-success alert-info">
<b>You can also mix with HTML</b></div>


```{tableofcontents}
```

# Introduction

Introduce your topic and how you are planning to tackle it. This section is about 1 page maximum.

You can add formula in a markdown cell:

$$
  \int_0^\infty \frac{x^3}{e^x-1}\,dx = \frac{\pi^4}{15}
$$


You can also have formula $x^2 + y^2$ embedded in your text.

**Using markdown to write text**

- You can use [markdown](https://www.markdownguide.org/cheat-sheet/)
- or MyST markdown works in Jupyter Notebooks as well. For more information about MyST markdown, check
out [the MyST guide in Jupyter Book](https://jupyterbook.org/content/myst.html),
or see [the MyST markdown documentation](https://myst-parser.readthedocs.io/en/latest/).

````{note}
Here is a note. It will render "properly" when generating your pages with `jupyter-book` using:
```
   jupyter-book build eScienceCourse_2021_AnneFouilloux/ --builder singlehtml
```
````

## Method
### Import Python packages

In [40]:
import xarray as xr
xr.set_options(display_style='html')
import intake
import cftime
from holoviews import opts
from bokeh.plotting import output_notebook
output_notebook()
import hvplot.xarray
import cmaps

Loading BokehJS ...

### Select and Read datasets
- Here you should explain which datasets you have been using, giving as much information as possible.

#### Open CMIP6 online catalog

In [17]:
cat_url = "https://storage.googleapis.com/cmip6/pangeo-cmip6.json"
col = intake.open_esm_datastore(cat_url)

#### Search and select corresponding data 

In [18]:
cat = col.search(source_id=['CESM2'], experiment_id=['historical'], table_id=['Amon'], variable_id=['tas'], member_id=['r1i1p1f1'])
cat.df

activity_id institution_id source_id experiment_id member_id table_id  \
0        CMIP           NCAR     CESM2    historical  r1i1p1f1     Amon   

  variable_id grid_label                                             zstore  \
0         tas         gn  gs://cmip6/CMIP6/CMIP/NCAR/CESM2/historical/r1...   

   dcpp_init_year   version  
0             NaN  20190308

#### Create dictionary from the list of datasets we found
- This step may take several minutes so be patient!

In [20]:
dset_dict = cat.to_dataset_dict(zarr_kwargs={'use_cftime':True})


--> The keys in the returned dictionary of datasets are constructed as follows:
	'activity_id.institution_id.source_id.experiment_id.table_id.grid_label'


#### Open dataset

- Use `xarray` python package to analyze netCDF dataset
- `open_dataset` allows to get all the metadata without loading data into memory. 
- with `xarray`, we only load into memory what is needed.

In [21]:
dset = dset_dict['CMIP.NCAR.CESM2.historical.Amon.gn']
dset

<xarray.Dataset>
Dimensions:    (lat: 192, lon: 288, member_id: 1, nbnd: 2, time: 1980)
Coordinates:
  * lat        (lat) float64 -90.0 -89.06 -88.12 -87.17 ... 88.12 89.06 90.0
    lat_bnds   (lat, nbnd) float32 dask.array<chunksize=(192, 2), meta=np.ndarray>
  * lon        (lon) float64 0.0 1.25 2.5 3.75 5.0 ... 355.0 356.2 357.5 358.8
    lon_bnds   (lon, nbnd) float32 dask.array<chunksize=(288, 2), meta=np.ndarray>
  * time       (time) object 1850-01-15 12:00:00 ... 2014-12-15 12:00:00
    time_bnds  (time, nbnd) object dask.array<chunksize=(1980, 2), meta=np.ndarray>
  * member_id  (member_id) <U8 'r1i1p1f1'
Dimensions without coordinates: nbnd
Data variables:
    tas        (member_id, time, lat, lon) float32 dask.array<chunksize=(1, 600, 192, 288), meta=np.ndarray>
Attributes: (12/48)
    Conventions:             CF-1.7 CMIP-6.2
    activity_id:             CMIP
    branch_method:           standard
    branch_time_in_child:    674885.0
    branch_time_in_parent:   219000.0
    case_id:                 15
    ...                      ...
    variable_id:             tas
    variant_info:            CMIP6 20th century experiments (1850-2014) with ...
    variant_label:           r1i1p1f1
    status:                  2019-10-25;created;by nhn2@columbia.edu
    intake_esm_varname:      ['tas']
    intake_esm_dataset_key:  CMIP.NCAR.CESM2.historical.Amon.gn

### Analysis Method

- explain here your method with references whenever necessary.

#### Mean over all dates

In [44]:
dmean = dset.mean("time", keep_attrs=True).squeeze()

## Results

### Visualization

- you can add metadata to your cells such as hide-input so that the code will only be shown when clicking on '+'

In [88]:
start_date = str(dset.time.min().dt.strftime("%b %Y").values)
end_date =  str(dset.time.max().dt.strftime("%b %Y").values)
p = dmean.tas.hvplot(
    cmap=cmaps.BlueYellowRed,
    geo=True,
    coastline='10m',
    frame_width=400,
    clabel='K',
    clim=(220,310) 
)
p.opts(opts.Overlay( title="Average " + dmean.tas.attrs['title'] +  ' (' + start_date + ' - ' + end_date + ')'))

:Overlay
   .Image.I     :Image   [lon,lat]   (tas)
   .Coastline.I :Feature   [Longitude,Latitude]

There is a lot more that you can do with outputs (such as including interactive outputs)
with your book. For more information about this, see [the Jupyter Book documentation](https://jupyterbook.org)

## Discussion

In this section, you should discuss your results (about 1 page).

You can [create a citation](https://jupyterbook.org/tutorials/references.html#create-a-citation) by adding new entries in the file `references.bib` and cite for instance:

```
{cite}`perez2011python`
```

Which would show the citation {cite}`perez2011python`.

## References

To add your bibliography add in a markdown cell:
    
````
```{bibliography}
```
````

```{bibliography}
```